In [1]:
# install package "varbvs" and load data
library(varbvs)
library(feather)

In [4]:
# trial
data(leukemia)
# names(leukemia)
print (leukemia$y)
fit <- varbvs(leukemia$x, NULL, leukemia$y, family = "binomial", logodds = seq(-3.5,-1,0.1), sa = 1)

Welcome to           --       *                              *               
VARBVS version 2.0.3 --       |              |               |               
large-scale Bayesian --       ||           | |    |          || |     |   |  
variable selection   -- |     || | |    |  | ||  ||        |||| ||    |   || 
****************************************************************************
Copyright (C) 2012-2017 Peter Carbonetto.
See http://www.gnu.org/licenses/gpl.html for the full license.
Fitting variational approximation for Bayesian variable selection model.
family:     binomial   num. hyperparameter settings: 26 
samples:    72         convergence tolerance         1.0e-04
variables:  3571       iid variable selection prior: yes 
covariates: 0          fit prior var. of coefs (sa): no 
intercept:  yes        fit approx. factors (eta):    yes 
Finding best initialization for 26 combinations of hyperparameters.
-iteration-   variational    max.   incl variance params
outer inner   low

In [21]:
names(fit)
# Compute Monte Carlo estimates of credible intervals for coefficients in the fitted variable selection model
varbvscoefcred(fit, vars=c("X3441", "X3038", "X2141", "X2230", "X951"))

[1] "family"       "n"            "n0"           "mu.cov"       "sa0"         
 [6] "update.sigma" "update.sa"    "optimize.eta" "prior.same"   "logw"        
[11] "sigma"        "sa"           "logodds"      "alpha"        "mu"          
[16] "s"            "eta"          "model.pve"

$a
[1] -3.34594044  0.16028592 -1.17297675  0.11170526  0.08885994

$b
[1] -2.17559567  1.18617102 -0.09570761  1.21135281  1.20279401

In [2]:
# read rds file
new <- readRDS("data/del_sim_scale5_shape1_N1000_M50_999.varbvs.rds")
names(new)
dim(new$mu)

[1] "family"       "n"            "n0"           "mu.cov"       "sa0"         
 [6] "update.sigma" "update.sa"    "optimize.eta" "prior.same"   "logw"        
[11] "sigma"        "sa"           "logodds"      "alpha"        "mu"          
[16] "s"            "eta"          "model.pve"    "summary"      "w"           
[21] "pip"          "beta"

[1] 11312    26

In [1]:
# get_summary <- function(datalist){
#     for (data in datalist){
#         newdat = readRDS(data)
#         print (newdat$summary$top.vars)
#     }
# }
# get_summary(c("data/del_sim_scaleNone_shapeNone_N1000_M50_999.varbvs.rds", 
#               "data/del_sim_scaleNone_shapeNone_N1000_M100_999.varbvs.rds", 
#               "data/del_sim_scale3_shape1_N1000_M50_999.varbvs.rds", 
#               "data/del_sim_scale3_shape1_N1000_M100_999.varbvs.rds", 
#               "data/del_sim_scale5_shape1_N1000_M50_999.varbvs.rds", 
#               "data/del_sim_scale5_shape1_N1000_M100_999.varbvs.rds"))

In [ ]:
# different prior for each gene, (1-pi)*p + pi*N(0,s^2)


In [3]:
# get summary of rds using pkl
# dat = as.matrix(feather::read_feather(${_input!r}))
dat = as.matrix(read_feather("data/del_sim_shape9_scale1_p0.005_N4000_M100_12.data.feather"))
print (dim(dat))

[1]  4000 21756


In [ ]:
fit = varbvs(dat[,-1], NULL, dat[,1], family = "binomial", logodds = seq(-3.5, -1, 0.1), sa = 1, verbose = F)

In [2]:
get_varbvs_rds <- function(datalist){
    for (dat in datalist){
        newdat = as.matrix(read_feather(dat))
        print (dim(newdat))
        newfit = varbvs(newdat[,-1], NULL, newdat[,1], family = "binomial", 
                        logodds = seq(-3.0,-1,0.1), sa = 1, verbose = F)
        newfit$summary = summary(newfit)
        newfit$w = normalizelogweights(newfit$logw)
        newfit$pip = newfit$alpha %*% c(newfit$w)
        newfit$beta = newfit$mu %*% c(newfit$w)
        newfit$var_names = colnames(newdat[-1])
        print (newfit$summary)
        filename = paste(dat, ".RDS", sep="")
        saveRDS(newfit, filename)
    }
}

In [ ]:
get_varbvs_rds(c("data/del_sim_shape9_scale1_p0.005_N4000_M100_12.data.feather",  
                 "data/del_sim_shape9_scale1_p0.005_N4000_M200_12.data.feather", 
                 "data/del_sim_shape5_scale1_p0.005_N4000_M100_12.data.feather", 
                 "data/del_sim_shape5_scale1_p0.005_N4000_M200_12.data.feather", 
                 "data/del_sim_shape3_scale1_p0.005_N4000_M100_12.data.feather", 
                 "data/del_sim_shape3_scale1_p0.005_N4000_M200_12.data.feather", 
                 "data/del_sim_shape5_scale1_p0.01_N4000_M100_12.data.feather",
                 "data/del_sim_shape3_scale1_p0.01_N4000_M100_12.data.feather", 
                 "data/del_sim_shape3_scale1_p0.01_N4000_M200_12.data.feather", 
                 "data/del_sim_shape9_scale1_p0.01_N4000_M100_12.data.feather", 
                 "data/del_sim_shape5_scale1_p0.01_N4000_M200_12.data.feather", 
                 "data/del_sim_shape9_scale1_p0.01_N4000_M200_12.data.feather"))

In [54]:
fit$summary = summary(fit)
fit$w = normalizelogweights(fit$logw)
fit$pip = fit$alpha %*% c(fit$w)
fit$beta = fit$mu %*% c(fit$w)
fit$var_names = colnames(dat[-1])

In [ ]:
saveRDS(fit, "data/del_sim_shape3_scale1_p0.01_N4000_M100_12.data.varbvs.rds")

In [45]:
aa <- readRDS("data/del_sim_shape3_scale1_p0.01_N4000_M100_12.data.varbvs.rds")
names(aa)
dim(aa$mu)

[1] "family"       "n"            "n0"           "mu.cov"       "sa0"         
 [6] "update.sigma" "update.sa"    "optimize.eta" "prior.same"   "logw"        
[11] "sigma"        "sa"           "logodds"      "alpha"        "mu"          
[16] "s"            "eta"          "model.pve"    "summary"      "w"           
[21] "pip"          "beta"

[1] 5046   26

In [14]:
dat1 = as.matrix(read_feather("data/del_test_data.feather"))
print (dim(dat1))

[1] 4000 4941


In [15]:
dat2 = as.matrix(read_feather("data/del_test_data_2.feather"))
print (dim(dat2))

[1] 4000 4941


In [18]:
all.equal(dat1, dat2)

[1] "Attributes: < Component “dimnames”: Component 2: 4940 string mismatches >"

In [19]:
all(dat1==dat2)

[1] TRUE

In [42]:
identical(dat1, dat2)

[1] FALSE

In [22]:
matequal <- function(x, y)
    is.matrix(x) && is.matrix(y) && dim(x) == dim(y) && all(x == y)

In [23]:
matequal(dat1, dat2)

[1] TRUE